In [1]:
!pip install opencv-python-headless
!pip install numpy

ERROR: Operation cancelled by user
ERROR: Operation cancelled by user
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/pip/_internal/cli/base_command.py", line 179, in exc_logging_wrapper
    status = run_func(*args)
             ^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/pip/_internal/cli/req_command.py", line 67, in wrapper
    return func(self, options, args)
           ^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/pip/_internal/commands/install.py", line 447, in run
    conflicts = self._determine_conflicts(to_install)
                ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/pip/_internal/commands/install.py", line 578, in _determine_conflicts
    return check_install_conflicts(to_install)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/pip/_internal/operations/check.py", line 101, in check_install_conflicts
 

In [2]:
from IPython.display import display, Javascript
from google.colab.output import eval_js

def check_camera():
    js = Javascript('''
        async function checkCamera() {
            try {
                const stream = await navigator.mediaDevices.getUserMedia({video: true});
                stream.getVideoTracks()[0].stop();
                return "Camera access successful!";
            } catch (err) {
                return "Error: " + err.message;
            }
        }
        checkCamera();
    ''')
    display(js)

check_camera()

<IPython.core.display.Javascript object>

In [5]:
from IPython.display import display, Javascript, HTML
from google.colab.output import eval_js
from base64 import b64decode, b64encode
import cv2
import numpy as np
import PIL
import io

# First, let's upload our reference image and video
from google.colab import files
print("Please upload an image from your book:")
uploaded_image = files.upload()

print("\nNow, please upload the video that should play:")
uploaded_video = files.upload()

# Get the filenames
reference_image_path = list(uploaded_image.keys())[0]
video_path = list(uploaded_video.keys())[0]

# Load and process reference image
reference_img = cv2.imread(reference_image_path, cv2.IMREAD_GRAYSCALE)
sift = cv2.SIFT_create()
kp1, des1 = sift.detectAndCompute(reference_img, None)

def show_video(video_path):
    """Display video in Colab"""
    video_html = f"""
    <video width="640" height="480" controls>
        <source src="data:video/mp4;base64,{b64encode(open(video_path, 'rb').read()).decode()}" type="video/mp4">
    </video>
    """
    return HTML(video_html)

def process_frame(frame):
    gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
    kp2, des2 = sift.detectAndCompute(gray, None)

    if des2 is not None and len(des2) > 0:
        bf = cv2.BFMatcher()
        matches = bf.knnMatch(des1, des2, k=2)

        good_matches = []
        for m, n in matches:
            if m.distance < 0.75 * n.distance:
                good_matches.append(m)

        return len(good_matches) > 30
    return False

def take_photo(filename='photo.jpg', quality=0.8):
    js = Javascript('''
        async function takePhoto(quality) {
            const div = document.createElement('div');
            const video = document.createElement('video');
            video.style.display = 'block';
            const stream = await navigator.mediaDevices.getUserMedia({video: true});
            document.body.appendChild(div);
            div.appendChild(video);
            video.srcObject = stream;
            await video.play();

            google.colab.output.setIframeHeight(document.documentElement.scrollHeight, true);

            const canvas = document.createElement('canvas');
            canvas.width = video.videoWidth;
            canvas.height = video.videoHeight;
            canvas.getContext('2d').drawImage(video, 0, 0);
            stream.getVideoTracks()[0].stop();
            div.remove();
            return canvas.toDataURL('image/jpeg', quality);
        }
        ''')
    display(js)
    data = eval_js('takePhoto({})'.format(quality))
    binary = b64decode(data.split(',')[1])

    image = PIL.Image.open(io.BytesIO(binary))
    opencv_image = cv2.cvtColor(np.array(image), cv2.COLOR_RGB2BGR)

    if process_frame(opencv_image):
        print("Image from book detected! Playing video...")
        display(show_video(video_path))
        return True
    return False

print("System ready! Point your camera at the book image.")
print("The video will play when the image is detected.")

# Main loop
while True:
    try:
        if take_photo():
            break  # Stop after successfully detecting image and playing video
    except KeyboardInterrupt:
        print("Stopped by user")
        break
    except Exception as err:
        print(str(err))
        break

Please upload an image from your book:


Saving IMG_20170416_104315.jpg to IMG_20170416_104315 (1).jpg

Now, please upload the video that should play:


Saving WhatsApp Video 2025-02-03 at 15.03.52_5cb131d1.mp4 to WhatsApp Video 2025-02-03 at 15.03.52_5cb131d1.mp4
System ready! Point your camera at the book image.
The video will play when the image is detected.


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Image from book detected! Playing video...
